![](https://github.com/bigdata-icict/ETL-Dataiku-DSS/raw/master/tutoriais/pcdas_1.5.png)

# Notebook para criação de tabela de indicadores da PNS - S 2019 Pré-natal - Parte 1

## Bibliotecas Utilizadas

In [ ]:
#Lendo pacotes necessários
library(survey)
library(ggplot2)
library(dplyr)
library(tictoc)
library(foreign)
library(forcats)
library(tidyverse)

## Carregando microdados da PNS

In [26]:
#Carregando banco de dados para R versão 3.5.0 ou superior
load("<coloque aqui o caminho para o arquivo dos microdados formato RDATA PNS 2019>")

#conferindo as dimensões (número de linhas e colunas)
dim("<Coloque aqui o nome do arquivo RDATA PNS 2019>")

[1] 293726   1087

## Definição do peso e filtragem de respondentes do questionário

In [27]:
#Selecionando registros válidos e calculando peso amostral - summary de verificação
pns2019.1<-  <Coloque aqui o nome do arquivo RDATA>  %>% filter(V0025A==1) 
pns2019.1<-pns2019.1 %>% mutate(peso_morador_selec=((V00291*(90846/168426190))))
pns2019.1<-pns2019.1 %>% filter(!is.na(peso_morador_selec))
summary(pns2019.1$peso_morador_selec)

    Min.  1st Qu.   Median     Mean  3rd Qu.     Max. 
 0.00562  0.26621  0.54401  1.00000  1.12765 61.09981 

## Criação de variáveis dos indicadores

In [31]:
# Desfechos - Indicadores

# 1. Proporção de mulheres que realizaram pré-natal - S001P.
pns2019.1$S001P <- NA
pns2019.1$S001P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068>0] <- 2
pns2019.1$S001P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 1
pns2019.1$S001P<-factor(pns2019.1$S001P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S001P)


# 2. Proporção de mulheres que realizaram pré-natal e que possuíam caderneta/cartão da gestante - S002P.
pns2019.1$S002P <- NA
pns2019.1$S002P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S002P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & pns2019.1$S075==1] <- 1
pns2019.1$S002P<-factor(pns2019.1$S002P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S002P)

# 3. Proporção de mulheres que iniciaram pré-natal com menos de 13 semanas ou até 3 meses de gestação - S003P.
pns2019.1$S003P <- NA
pns2019.1$S003P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S003P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & (pns2019.1$S06902 <= 3 | pns2019.1$S06901 < 13)] <- 1
pns2019.1$S003P<-factor(pns2019.1$S003P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S003P)

# 4. Proporção de mulheres que tiveram 6 ou mais consultas de pré-natal entre as gestantes com parto a termo ou pós-termo - S004P.
pns2019.1$S004P <- NA
pns2019.1$S004P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & pns2019.1$S11801>=37] <- 2
pns2019.1$S004P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1 & pns2019.1$S11801>=37 & (pns2019.1$S070>=6 & pns2019.1$S070<8)] <- 1
pns2019.1$S004P<-factor(pns2019.1$S004P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S004P)

# 5. Proporção de mulheres que realizaram a maioria das consultas de pré-natal em estabelecimentos públicos de saúde - S005P.
pns2019.1$S005P <- NA
pns2019.1$S005P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1] <- 2
pns2019.1$S005P[pns2019.1$C006==2 & pns2019.1$C008>=18 & pns2019.1$S068==1  & (pns2019.1$S071 <=2 | pns2019.1$S071 <=4)] <- 1
pns2019.1$S005P<-factor(pns2019.1$S005P, levels=c(1,2), labels=c("Sim","Não"))
summary(pns2019.1$S005P)

Sim   Não  NA's 
 2734    84 88028

Sim   Não  NA's 
 2657    77 88112

Sim   Não  NA's 
 2356   378 88112

Sim   Não  NA's 
 1822   251 88773

Sim   Não  NA's 
 2056   678 88112

## Definições de abrangências

### Situação urbana ou rural

In [6]:
#Situação Urbano ou Rural
pns2019.1 <- pns2019.1 %>% rename(Sit_Urbano_Rural=V0026)
pns2019.1$Sit_Urbano_Rural<-factor(pns2019.1$Sit_Urbano_Rural, levels=c(1,2), labels=c("urbano", "rural"))
summary(pns2019.1$Sit_Urbano_Rural)

urbano  rural 
 69873  20973

### UF

In [7]:
#Estados - UFs
pns2019.1 <- pns2019.1 %>% rename(Unidades_da_Federacao=V0001)
pns2019.1$Unidades_da_Federacao<-factor(pns2019.1$Unidades_da_Federacao, levels=c(11,12,13,14,15,16,17,21,22,23,24,25,26,27,28,29,31,32,33,35,41,42,43,50,51,52,53),
                                       label=c("Rondônia","Acre","Amazonas","Roraima","Pará","Amapá","Tocantins","Maranhão","Piauí","Ceará",
                                        "Rio Grande do Norte","Paraíba","Pernambuco","Alagoas","Sergipe","Bahia",
                                        "Minas Gerais","Espírito Santo","Rio de Janeiro","São Paulo",
                                        "Paraná","Santa Catarina","Rio Grande do Sul", 
                                        "Mato Grosso do Sul","Mato Grosso","Goiás","Distrito Federal"))
summary(pns2019.1$Unidades_da_Federacao)

Rondônia                Acre            Amazonas             Roraima 
               2176                2380                3479                2238 
               Pará               Amapá           Tocantins            Maranhão 
               3853                1554                1922                5080 
              Piauí               Ceará Rio Grande do Norte             Paraíba 
               2740                4265                2962                3158 
         Pernambuco             Alagoas             Sergipe               Bahia 
               4083                2987                2610                3659 
       Minas Gerais      Espírito Santo      Rio de Janeiro           São Paulo 
               5209                3541                4966                6114 
             Paraná      Santa Catarina   Rio Grande do Sul  Mato Grosso do Sul 
               3967                3738                3767                2863 
        Mato Grosso               Goiás    Distrito Federal 
               2468                2702                2365

### Grandes Regiões

In [8]:
#Grandes Regiões
pns2019.1 <- pns2019.1 %>% 
  mutate(GrandesRegioes = fct_collapse(Unidades_da_Federacao, 
                                          `Norte` = c("Rondônia","Acre","Amazonas","Roraima","Pará", "Amapá","Tocantins"),
                                          `Nordeste` = c("Maranhão", "Piauí", "Ceará", "Rio Grande do Norte", "Paraíba","Pernambuco", "Alagoas","Sergipe","Bahia"),
                                          `Sudeste` = c("Minas Gerais", "Espírito Santo","Rio de Janeiro", "São Paulo"), 
                                          `Sul` = c("Paraná", "Santa Catarina", "Rio Grande do Sul"),
                                          `Centro-Oeste`= c("Mato Grosso do Sul","Mato Grosso", "Goiás", "Distrito Federal")))
summary(pns2019.1$GrandesRegioes)

Norte     Nordeste      Sudeste          Sul Centro-Oeste 
       17602        31544        19830        11472        10398

### Capital

In [9]:
#Capital
pns2019.1<- pns2019.1 %>% mutate(Capital= fct_collapse(Unidades_da_Federacao,
                                        `Porto Velho`= "Rondônia", 
                                        `Boa Vista`= "Roraima",              
                                        `Rio Branco`= "Acre", 
                                        `Manaus` = "Amazonas",
                                        `Belém` = "Pará" ,
                                        `Macapá`= "Amapá",
                                        `Palmas` = "Tocantins",
                                        `São Luís` = "Maranhão",
                                        `Teresina`= "Piauí" ,
                                        `Fortaleza`= "Ceará",
                                        `Natal`= "Rio Grande do Norte",
                                        `João Pessoa`= "Paraíba",
                                        `Recife`= "Pernambuco",
                                        `Maceió`= "Alagoas",
                                        `Aracaju`= "Sergipe",
                                        `Salvador`= "Bahia",
                                        `Belo Horizonte`= "Minas Gerais",
                                        `Vitória`= "Espírito Santo",
                                        `Rio de Janeiro`= "Rio de Janeiro",
                                        `São Paulo`= "São Paulo",
                                        `Curitiba`= "Paraná",
                                        `Florianópolis`= "Santa Catarina",
                                        `Porto Alegre`= "Rio Grande do Sul",
                                        `Campo Grande`=  "Mato Grosso do Sul",
                                        `Cuiabá`= "Mato Grosso",
                                        `Goiânia` = "Goiás",
                                        `Brasília`= "Distrito Federal"))
summary(pns2019.1$Capital)

Porto Velho     Rio Branco         Manaus      Boa Vista          Belém 
          2176           2380           3479           2238           3853 
        Macapá         Palmas       São Luís       Teresina      Fortaleza 
          1554           1922           5080           2740           4265 
         Natal    João Pessoa         Recife         Maceió        Aracaju 
          2962           3158           4083           2987           2610 
      Salvador Belo Horizonte        Vitória Rio de Janeiro      São Paulo 
          3659           5209           3541           4966           6114 
      Curitiba  Florianópolis   Porto Alegre   Campo Grande         Cuiabá 
          3967           3738           3767           2863           2468 
       Goiânia       Brasília 
          2702           2365

### Faixa Etária

In [10]:
#Faixas Etárias
pns2019.1 <- pns2019.1 %>% mutate(fx_idade_S=cut(C008,
  breaks = c(18,25,30,40,120),
  labels = c("18 a 24 anos", "25 a 29 anos", "30 a 39 anos", "40 anos ou mais"), 
  ordered_result = TRUE, right = FALSE))
summary(pns2019.1$fx_idade_S)

18 a 24 anos    25 a 29 anos    30 a 39 anos 40 anos ou mais            NA's 
           8145            7249           18150           54987            2315

### Raça

In [11]:
#Raça
pns2019.1 <- pns2019.1 %>% mutate(Raca= ifelse(C009==1, 1, 
                        ifelse(C009==2, 2, 
                            ifelse(C009==4, 3, 9))))

pns2019.1$Raca<-factor(pns2019.1$Raca, levels=c(1,2,3),labels=c("Branca", "Preta", "Parda"))

summary(pns2019.1$Raca)

Branca  Preta  Parda   NA's 
 33133  10345  45994   1374

### Renda per capita

In [12]:
#Rendimento domiciliar per capita
pns2019.1 <- pns2019.1 %>% mutate(rend_per_capita = ifelse(VDF004 %in% 1:2, 1, 
                        ifelse(VDF004%in% 3, 2, 
                        ifelse(VDF004%in% 4, 3,
                        ifelse(VDF004%in% 5, 4, 
                        ifelse(is.na(VDF004)==TRUE, NA_real_, 5))))))

pns2019.1$rend_per_capita<-factor(pns2019.1$rend_per_capita, levels=c(1,2,3,4,5), labels=c("Até 1/2 SM","1/2 até 1 SM","1 até 2 SM",
                                                                                   "2 até 3 SM","Mais de 3 SM"))
summary(pns2019.1$rend_per_capita)


Até 1/2 SM 1/2 até 1 SM   1 até 2 SM   2 até 3 SM Mais de 3 SM         NA's 
       23697        26406        22466         7612        10643           22

### Escolaridade

In [13]:
# Escolaridade
pns2019.1 <- pns2019.1 %>% mutate(gescol = ifelse(VDD004A %in% 1:2, 1, 
                        ifelse(VDD004A%in% 3:4, 2, 
                        ifelse(VDD004A%in% 5:6, 3,4
                        ))))

pns2019.1$gescol<-factor(pns2019.1$gescol, levels=c(1,2,3,4), 
                                  labels=c("Fundamental incompleto ou equivalente","Médio incompleto ou equivalente",
                                           "Superior incompleto ou equivalente","Superior completo"))
summary(pns2019.1$gescol)

Fundamental incompleto ou equivalente       Médio incompleto ou equivalente 
                                36276                                 13520 
   Superior incompleto ou equivalente                     Superior completo 
                                27433                                 13617

## Criando indicadores

### Filtrando base de indicadores

In [14]:
#Selecionando variáveis para cálculo de indicadores no survey
pns2019Ssurvey<- pns2019.1 %>% select("V0024","UPA_PNS","peso_morador_selec", "S001P", "S002P", "S003P",
       "S004P", "S005P", "C008", "C006", "C009", "S068", "S11801", "S118",
       "V0031", "Sit_Urbano_Rural", "Unidades_da_Federacao",
       "GrandesRegioes",  "Capital", "fx_idade_S", "Raca",
       "rend_per_capita", "gescol") #"Sexo", 
summary(pns2019Ssurvey)

     V0024            UPA_PNS      peso_morador_selec  S001P        S002P      
 1210010: 1167   140001681:   18   Min.   : 0.00562   Sim : 2734   Sim : 2657  
 1410011:  792   140003815:   18   1st Qu.: 0.26621   Não :   84   Não :   77  
 2710111:  779   140005777:   18   Median : 0.54401   NA's:88028   NA's:88112  
 2410011:  745   140006746:   18   Mean   : 1.00000                            
 5010011:  738   140007081:   18   3rd Qu.: 1.12765                            
 3210011:  711   140007715:   18   Max.   :61.09981                            
 (Other):85914   (Other)  :90738                                               
  S003P        S004P        S005P            C008             C006      
 Sim : 2356   Sim : 2073   Sim : 2056   Min.   : 15.00   Min.   :1.000  
 Não :  378   Não :  661   Não :  678   1st Qu.: 32.00   1st Qu.:1.000  
 NA's:88112   NA's:88112   NA's:88112   Median : 45.00   Median :2.000  
                                        Mean   : 46.39   Mean   :1.5

### Exporta tabela filtrada com os dados específicos - Módulo S 2019 - Parte 1

In [15]:
#Salvando csv para cálculo de indicadores no survey
diretorio_saida <- "<coloque aqui o diretório>"
write.csv(pns2019Ssurvey, file.path(diretorio_saida, "pns2019Ssurvey.csv"))

### Cria plano amostral complexo

In [16]:
desPNS=svydesign(id=~UPA_PNS, strat=~V0024, weight=~peso_morador_selec, nest=TRUE, 
                 data=pns2019Ssurvey)

In [17]:
#survey design S001P
desPNSS001P=subset(desPNS, C006==2 & C008>=18 & S068>0)
desPNSS001P_C=subset(desPNS, C006==2 & C008>=18 & S068>0 & V0031==1)
desPNSS001P_R=subset(desPNS, C006==2 & C008>=18 & S068>0 & !is.na(Raca))

In [18]:
#survey design S002P, S003P, S005P
desPNSS002P=subset(desPNS, C006==2 & C008>=18 & S068==1)
desPNSS002P_C=subset(desPNS, C006==2 & C008>=18 & S068==1 & V0031==1)
desPNSS002P_R=subset(desPNS, C006==2 & C008>=18 & S068==1 & !is.na(Raca)) 

In [19]:
#survey design S004P
desPNSS004P=subset(desPNS, C006==2 & C008>=18 & (S068==1 & S11801>=37))
desPNSS004P_C=subset(desPNS, C006==2 & C008>=18 & (S068==1 & S11801>=37) & V0031==1) 
desPNSS004P_R=subset(desPNS, C006==2 & C008>=18 & (S068==1 & S11801>=37) & !is.na(Raca))

### Criação da tabela de indicadores
Essa tabela é responsável por unir os indicadores no formato do painel de indicadores

In [20]:
matrizIndicadores = data.frame()

#### Definição de variáveis para iteração dos indicadores

In [21]:
ListaIndicadores = c(~S001P, ~S002P, ~S003P, ~S004P, ~S005P)
ListaIndicadoresTexto = c("S001P", "S002P", "S003P", "S004P", "S005P" )
ListaTotais = c('Brasil','Capital')
Ano <- "2019"

In [22]:
ListaDominiosS001 = c(~Raca,~rend_per_capita,~fx_idade_S,~Sit_Urbano_Rural,
                      ~Unidades_da_Federacao,~GrandesRegioes,~Capital,
                      ~gescol)
ListaDominiosTextoS001= c("raça","rend_per_capita","fx_idade_S","urb_rur",
                          "uf","região","capital","gescol") 

#### Preenchendo a tabela de indicadores
Essas iterações rodam por indicador, abrangência e por design

In [23]:
#Cálculo dos indicadores usando o pacote survey 
i <- 0
#Para cada indicador
for( indicador in ListaIndicadores){
    i <- i + 1; j <- 1
    if (ListaIndicadoresTexto[i]== "S001P" | 
        ListaIndicadoresTexto[i]== "S002P" | 
        ListaIndicadoresTexto[i]== "S003P" | 
        ListaIndicadoresTexto[i]== "S004P" | 
        ListaIndicadoresTexto[i]== "S005P"){
        ListaDominios<-ListaDominiosS001
        ListaDominiosTexto<-ListaDominiosTextoS001
        } else {
                    ListaDominios<-ListaDominiosS001
ListaDominiosTexto<-ListaDominiosTextoS001
                }
    #Para cada dominio
    for (dominio in ListaDominios){
#design especifico para capital que é subconjunto do dataframe total
         if (ListaDominiosTexto[j]=="capital"){
#designs especificos por variavel que são subconjuntos do dataset total
            if (ListaIndicadoresTexto[i]== "S002P" |
                ListaIndicadoresTexto[i]== "S003P" |
                ListaIndicadoresTexto[i]== "S005P"){
              dataframe_indicador<-svyby( indicador , dominio , desPNSS002P_C , svymean,vartype= c("ci","cv")) 
              } else if (ListaIndicadoresTexto[i]== "S001P") {
                  dataframe_indicador<-svyby( indicador , dominio , desPNSS001P_C , svymean,vartype= c("ci","cv"))
                 } else if (ListaIndicadoresTexto[i]== "S004P") {
                    dataframe_indicador<-svyby( indicador , dominio , desPNSS004P_C, svymean,vartype= c("ci","cv"))
                        }
               } else if  (ListaDominiosTexto[j]=="raça"){
                    if (ListaIndicadoresTexto[i]== "S002P" |
                        ListaIndicadoresTexto[i]== "S003P" |
                        ListaIndicadoresTexto[i]== "S005P"){
                            dataframe_indicador<-svyby( indicador , dominio , desPNSS002P_R , svymean,vartype= c("ci","cv"))
                        } else if
(ListaIndicadoresTexto[i]== "S001P"){
                            dataframe_indicador<-svyby( indicador , dominio , desPNSS001P_R , svymean,vartype= c("ci","cv"))
                        } else if
(ListaIndicadoresTexto[i]== "S004P"){
                            dataframe_indicador<-svyby( indicador , dominio , desPNSS004P_R , svymean,vartype= c("ci","cv"))
                        }
               #design geral para o subconjunto maior que 15 anos
                 } else { 
                        if (ListaIndicadoresTexto[i]== "S002P" |
                            ListaIndicadoresTexto[i]== "S003P" |
                            ListaIndicadoresTexto[i]== "S005P"){
                                dataframe_indicador<-svyby( indicador , dominio , desPNSS002P , svymean,vartype= c("ci","cv"))
                            } else if
(ListaIndicadoresTexto[i]== "S001P"){
                            dataframe_indicador<-svyby( indicador , dominio , desPNSS001P , svymean,vartype= c("ci","cv"))
                        } else if
(ListaIndicadoresTexto[i]== "S004P")
                     {
                                dataframe_indicador<-svyby( indicador , dominio , desPNSS004P , svymean,vartype= c("ci","cv"))
                            }
                        }
#União do dataframe de indicadores no formato do painel disponibilizado para PNS
dataframe_indicador<-data.frame(dataframe_indicador)
               colnames(dataframe_indicador) <- c("abr_nome","Sim","Nao","LowerS","LowerN","UpperS","UpperN","cvS","cvN")
               dataframe_indicador$Indicador <- ListaIndicadoresTexto[i]
               dataframe_indicador$abr_tipo <- ListaDominiosTexto[j]
               dataframe_indicador$Ano <- Ano
               dataframe_indicador <- dataframe_indicador %>% select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS","cvS")
               matrizIndicadores <-rbind(matrizIndicadores,dataframe_indicador)
               j <- j + 1
    }
}

#### Criando a tabela pela abrangência total

In [24]:
matriz_totais <- data.frame()

#### Preenchendo a tabela com as abrangencia Brasil e total das capitais

In [25]:
i <- 0
#para cada indicador
for(indicador in ListaIndicadores){
    i <- i + 1
    #para os totais Brasil e total das capitais
    for(total in ListaTotais){
        dataframe_indicador <- data.frame()
        dataframe_indicador_S <- data.frame()
        #Uso do design que é subconjunto do dataset para cada Capital
        if (total == "Capital"){
                #Indicadores que são subconjunto do dataset total
                if (ListaIndicadoresTexto[i]== "S002P" |
                    ListaIndicadoresTexto[i]== "S003P" |
                    ListaIndicadoresTexto[i]== "S005P"){
                            dataframe_indicador <- svymean(indicador,desPNSS002P_C)
                        } else if
(ListaIndicadoresTexto[i]== "S001P"){
                            dataframe_indicador <- svymean(indicador,desPNSS001P_C)
                        } else if
(ListaIndicadoresTexto[i]== "S004P"){
                            dataframe_indicador <- svymean(indicador,desPNSS004P_C)
                    }
                } else {
                if (ListaIndicadoresTexto[i]== "S002P" |
                    ListaIndicadoresTexto[i]== "S003P" |
                    ListaIndicadoresTexto[i]== "S005P"){
                            dataframe_indicador <- svymean(indicador,desPNSS002P)
                        } else if (ListaIndicadoresTexto[i]== "S001P"){
                            dataframe_indicador <- svymean(indicador,desPNSS001P)
                        } else if
(ListaIndicadoresTexto[i]== "S004P"){
                            dataframe_indicador <- svymean(indicador,desPNSS004P)
                    }
                }
        intervalo_confianca <- confint(dataframe_indicador)
        coeficiente_variacao <- cv(dataframe_indicador)
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(intervalo_confianca))
        dataframe_indicador <- cbind(data.frame(dataframe_indicador),data.frame(coeficiente_variacao))
        
        dataframe_indicador <- dataframe_indicador %>% 
                               select('mean','X2.5..','X97.5..',coeficiente_variacao) 
        dataframe_indicador_S <- dataframe_indicador %>% 
                                 slice(1)
                
        colnames(dataframe_indicador_S) <- c('Sim','LowerS','UpperS', 'cvS')
        dataframe_indicador_S$Indicador <- ListaIndicadoresTexto[i]
        
        dataframe_indicador_S$abr_tipo <- "total"
        dataframe_indicador_S$abr_nome <- total
        dataframe_indicador_S$Ano <- Ano 
        dataframe_indicador_S <- dataframe_indicador_S %>% 
                             select("abr_tipo","abr_nome","Ano","Indicador","Sim","LowerS","UpperS",'cvS')
        
        matriz_totais <-rbind(matriz_totais,dataframe_indicador_S)
    }
}

In [26]:
matriz_totais

abr_tipo abr_nome Ano  Indicador Sim       LowerS    UpperS   
S001PSim  total    Brasil   2019 S001P     0.9802181 0.9735800 0.9868562
S001PSim1 total    Capital  2019 S001P     0.9806496 0.9721002 0.9891990
S002PSim  total    Brasil   2019 S002P     0.9624012 0.9492620 0.9755404
S002PSim1 total    Capital  2019 S002P     0.9341446 0.9050284 0.9632609
S003PSim  total    Brasil   2019 S003P     0.8814929 0.8630816 0.8999041
S003PSim1 total    Capital  2019 S003P     0.8898081 0.8547462 0.9248701
S004PSim  total    Brasil   2019 S004P     0.8939233 0.8748669 0.9129797
S004PSim1 total    Capital  2019 S004P     0.9086737 0.8785255 0.9388218
S005PSim  total    Brasil   2019 S005P     0.6712686 0.6383040 0.7042333
S005PSim1 total    Capital  2019 S005P     0.5467601 0.4924781 0.6010420
          cvS        
S001PSim  0.003455195
S001PSim1 0.004448070
S002PSim  0.006965703
S002PSim1 0.015902776
S003PSim  0.010656560
S003PSim1 0.020104431
S004PSim  0.010876579
S004PSim1 0.016927946
S005PSim  0.025055548
S005PSim1 0.050653646

#### Unindo tabela de indicadores e de totais

In [27]:
matrizIndicadores<-rbind(matrizIndicadores,matriz_totais)

#### Visualizando tabela de indicadores

In [28]:
matrizIndicadores

abr_tipo       
Branca                                 raça           
Preta                                  raça           
Parda                                  raça           
Até 1/2 SM                             rend_per_capita
1/2 até 1 SM                           rend_per_capita
1 até 2 SM                             rend_per_capita
2 até 3 SM                             rend_per_capita
Mais de 3 SM                           rend_per_capita
18 a 24 anos                           fx_idade_S     
25 a 29 anos                           fx_idade_S     
30 a 39 anos                           fx_idade_S     
40 anos ou mais                        fx_idade_S     
urbano                                 urb_rur        
rural                                  urb_rur        
Rondônia                               uf             
Acre                                   uf             
Amazonas                               uf             
Roraima                                uf             
Pará                                   uf             
Amapá                                  uf             
Tocantins                              uf             
Maranhão                               uf             
Piauí                                  uf             
Ceará                                  uf             
Rio Grande do Norte                    uf             
Paraíba                                uf             
Pernambuco                             uf             
Alagoas                                uf             
Sergipe                                uf             
Bahia                                  uf             
⋮                                      ⋮              
João Pessoa4                           capital        
Recife4                                capital        
Maceió4                                capital        
Aracaju4                               capital        
Salvador4                              capital        
Belo Horizonte4                        capital        
Vitória4                               capital        
Rio de Janeiro9                        capital        
São Paulo8                             capital        
Curitiba4                              capital        
Florianópolis4                         capital        
Porto Alegre4                          capital        
Campo Grande4                          capital        
Cuiabá4                                capital        
Goiânia4                               capital        
Brasília4                              capital        
Fundamental incompleto ou equivalente4 gescol         
Médio incompleto ou equivalente4       gescol         
Superior incompleto ou equivalente4    gescol         
Superior completo4                     gescol         
S001PSim                               total          
S001PSim1                              total          
S002PSim                               total          
S002PSim1                              total          
S003PSim                               total          
S003PSim1                              total          
S004PSim                               total          
S004PSim1                              total          
S005PSim                               total          
S005PSim1                              total          
                                       abr_nome                             
Branca                                 Branca                               
Preta                                  Preta                                
Parda                                  Parda                                
Até 1/2 SM                             Até 1/2 SM                           
1/2 até 1 SM                           1/2 até 1 SM                         
1 até 2 SM                             1 até 2 SM                           
2 até 3 SM                             2 até 3 SM                           
Mais de 3 SM 

#### Exportando tabela de indicadores calculados - Módulo S 2019

In [30]:
diretorio_saida <- "<coloque aqui o diretório>"
write.table(matrizIndicadores,file=paste0(diretorio_saida,"Indicadores_2019S_R.csv"),sep = ";",dec = ",",row.names = FALSE)